In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt
from functools import reduce
import json
from IPython.display import display, Markdown

In [2]:
sample_submission=pd.read_csv("../data/raw/sample_submission.csv")
specs=pd.read_csv("../data/raw/specs.csv")
test=pd.read_csv("../data/raw/test.csv")
train=pd.read_csv("../data/raw/train.csv")
train_labels=pd.read_csv("../data/raw/train_labels.csv")

Those games roughly correspond to assessments which should be predicted. Looks like activities are given not for learning, but for relaxation (like fireworks).

In [3]:
train.title[train.type=="Game"].unique()

array(['Scrub-A-Dub', 'Dino Drink', 'All Star Sorting', 'Air Show',
       'Crystals Rule', 'Bubble Bath', 'Dino Dive', 'Chow Time',
       'Pan Balance', 'Happy Camel', 'Leaf Leader'], dtype=object)

In [4]:
train.title[train.type=="Assessment"].unique()

array(['Mushroom Sorter (Assessment)', 'Bird Measurer (Assessment)',
       'Cauldron Filler (Assessment)', 'Cart Balancer (Assessment)',
       'Chest Sorter (Assessment)'], dtype=object)

In [6]:
def show_game_session(df, title, filter_cols=tuple()):
    random_row = df[df.title == title].sample(1)
    installation_id = random_row.installation_id.iloc[0]
    session_id = random_row.game_session.iloc[0]
    show_player_sessions(df, installation_id, session_id, filter_cols)


def show_player_sessions(df, installation_id, session_id=None, filter_cols=tuple()):
    df = df[df.installation_id == installation_id].copy()
    game_sessions = [session_id] if session_id else df.game_session.unique()
    for game_session in game_sessions:
        session = df[df.game_session==game_session].copy()
        display(Markdown(describe_session(game_session, session)))
        with pd.option_context('display.max_rows', 999, 'display.max_columns', 999, 
                               'display.max_colwidth', 999):
            display(format_session(session, filter_cols))


def describe_session(game_session, session):
    head = session.sort_values("event_count").head(1)
    if "version" in json.loads(head.event_data.iloc[0]):
        version = json.loads(head.event_data.iloc[0])["version"]
    else:
        version = "-"
    return f"__{game_session} {head.title.iloc[0]} {head.type.iloc[0]} {head.world.iloc[0]} v{version}__ "


def format_session(session, filter_cols):
    session = session.sort_values("event_count")
    session["timestamp"]=session["timestamp"].str[:19]
    session["event_data"] = session.event_data.apply(json.loads)
    columns = sorted(reduce(set.__or__, session.event_data.apply(lambda d: set(d.keys())).values))
    for c in columns:
        session[c] = session.event_data.apply(lambda x: x.get(c, '-'))
    session["version"]=None
    session = session.drop(["game_session", "installation_id", "event_data", "game_time", 
                            "title", "type", "world", "version"] + [c for c in filter_cols if c in session.columns], axis=1)
    session.set_index("event_count", inplace=True)
    
    return session


for game in test.title[test.type=="Game"].unique():
    show_game_session(train, game, ["coordinates"])

__4c8b2da4e5c8ce7f Chow Time Game CRYSTALCAVES v1.0__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            7d093bf9  2019-10-03T21:25:02        2000       -   
2            f93fc684  2019-10-03T21:25:05        4010       -   
3            7ec0c298  2019-10-03T21:25:07        3010       -   
4            0d1da71f  2019-10-03T21:25:17        3110       -   
5            63f13dd7  2019-10-03T21:25:17        2020       -   
6            7ec0c298  2019-10-03T21:25:17        3010       -   
7            0d1da71f  2019-10-03T21:25:33        3110       -   
8            0330ab6a  2019-10-03T21:25:36        3020       -   
9            cfbd47c8  2019-10-03T21:25:38        4030       -   
10           d185d3ea  2019-10-03T21:25:40        4035       -   
11           7372e1a5  2019-10-03T21:25:41        4070       -   
12           2230fab4  2019-10-03T21:25:42        3120       -   
13           cfbd47c8  2019-10-03T21:25:42        4030       -   
14           4ef8cdd3  2019-10-03T21:25:43        4020   False   
15           0330ab6a  2019-10-03T21:25:44        3020       -   
16           cfbd47c8  2019-10-03T21:25:45        4030       -   
17           2230fab4  2019-10-03T21:25:46        3120       -   
18           0330ab6a  2019-10-03T21:25:46        3020       -   
19           d185d3ea  2019-10-03T21:25:46        4035       -   
20           cfbd47c8  2019-10-03T21:25:47        4030       -   
21           4ef8cdd3  2019-10-03T21:25:49        4020    True   
22           2230fab4  2019-10-03T21:25:49        3120       -   
23           0330ab6a  2019-10-03T21:25:49        3020       -   
24           cfbd47c8  2019-10-03T21:25:52        4030       -   
25           4ef8cdd3  2019-10-03T21:25:52        4020    True   
26           7372e1a5  2019-10-03T21:25:53        4070       -   
27           2230fab4  2019-10-03T21:25:53        3120       -   
28           0330ab6a  2019-10-03T21:25:53        3020       -   
29           cfbd47c8  2019-10-03T21:25:55        4030       -   
30           2230fab4  2019-10-03T21:25:55        3120       -   
31           0330ab6a  2019-10-03T21:25:55        3020       -   
32           d185d3ea  2019-10-03T21:25:56        4035       -   
33           7372e1a5  2019-10-03T21:25:57        4070       -   
34           cfbd47c8  2019-10-03T21:25:57        4030       -   
35           4ef8cdd3  2019-10-03T21:25:58        4020   False   
36           2230fab4  2019-10-03T21:26:00        3120       -   
37           0330ab6a  2019-10-03T21:26:00        3020       -   
38           cfbd47c8  2019-10-03T21:26:01        4030       -   
39           2230fab4  2019-10-03T21:26:02        3120       -   
40           0330ab6a  2019-10-03T21:26:02        3020       -   
41           d185d3ea  2019-10-03T21:26:03        4035       -   
42           7372e1a5  2019-10-03T21:26:03        4070       -   
43           cfbd47c8  2019-10-03T21:26:04        4030       -   
44           2230fab4  2019-10-03T21:26:05        3120       -   
45           0330ab6a  2019-10-03T21:26:05        3020       -   
46           d185d3ea  2019-10-03T21:26:05        4035       -   
47           7372e1a5  2019-10-03T21:26:06        4070       -   
48           cfbd47c8  2019-10-03T21:26:07        4030       -   
49           4ef8cdd3  2019-10-03T21:26:08        4020    True   
50           2230fab4  2019-10-03T21:26:09        3120       -   
51           0330ab6a  2019-10-03T21:26:09        3020       -   
52           cfbd47c8  2019-10-03T21:26:09        4030       -   
53           4ef8cdd3  2019-10-03T21:26:10        4020    True   
54           2230fab4  2019-10-03T21:26:11        3120       -   
55           0330ab6a  2019-10-03T21:26:11        3020       -   
56           cfbd47c8  2019-10-03T21:26:13        4030       -   
57           4ef8cdd3  2019-10-03T21:26:15        4020    True   
58           56817e2b  2019-10-03T21:26:15        2030       -   
59           2230fab4  2019-10-03T21:26:15        312

__d26d994165ccfe2e All Star Sorting Game TREETOPCITY v1.0__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            b7dc8128  2019-08-17T21:15:03        2000       -   
2            4b5efe37  2019-08-17T21:15:05        4010       -   
3            2c4e6db0  2019-08-17T21:15:07        2020       -   
4            363d3849  2019-08-17T21:15:07        3010       -   
5            587b5989  2019-08-17T21:15:10        4070       -   
6            9e4c8c7b  2019-08-17T21:15:11        3110       -   
7            363d3849  2019-08-17T21:15:11        3010       -   
8            587b5989  2019-08-17T21:15:12        4070       -   
9            587b5989  2019-08-17T21:15:12        4070       -   
10           587b5989  2019-08-17T21:15:13        4070       -   
11           587b5989  2019-08-17T21:15:15        4070       -   
12           9e4c8c7b  2019-08-17T21:15:15        3110       -   
13           1cc7cfca  2019-08-17T21:15:16        4030       -   
14           d02b7a8e  2019-08-17T21:15:16        4035       -   
15           1cc7cfca  2019-08-17T21:15:16        4030       -   
16           2dc29e21  2019-08-17T21:15:17        4020    True   
17           1cc7cfca  2019-08-17T21:15:19        4030       -   
18           2dc29e21  2019-08-17T21:15:21        4020    True   
19           1cc7cfca  2019-08-17T21:15:22        4030       -   
20           2dc29e21  2019-08-17T21:15:23        4020    True   
21           ca11f653  2019-08-17T21:15:24        2030       -   
22           daac11b0  2019-08-17T21:15:26        3021       -   
23           1f19558b  2019-08-17T21:15:29        3121       -   
24           2c4e6db0  2019-08-17T21:15:29        2020       -   
25           363d3849  2019-08-17T21:15:29        3010       -   
26           9e4c8c7b  2019-08-17T21:15:33        3110       -   
27           1cc7cfca  2019-08-17T21:15:33        4030       -   
28           2dc29e21  2019-08-17T21:15:35        4020    True   
29           1cc7cfca  2019-08-17T21:15:36        4030       -   
30           2dc29e21  2019-08-17T21:15:37        4020    True   
31           587b5989  2019-08-17T21:15:38        4070       -   
32           1cc7cfca  2019-08-17T21:15:39        4030       -   
33           2dc29e21  2019-08-17T21:15:41        4020    True   
34           587b5989  2019-08-17T21:15:43        4070       -   
35           1cc7cfca  2019-08-17T21:15:43        4030       -   
36           2dc29e21  2019-08-17T21:15:45        4020    True   
37           ca11f653  2019-08-17T21:15:45        2030       -   
38           daac11b0  2019-08-17T21:15:48        3021       -   
39           1f19558b  2019-08-17T21:15:51        3121       -   
40           2c4e6db0  2019-08-17T21:15:51        2020       -   
41           363d3849  2019-08-17T21:15:51        3010       -   
42           587b5989  2019-08-17T21:15:54        4070       -   
43           587b5989  2019-08-17T21:15:55        4070       -   
44           9e4c8c7b  2019-08-17T21:15:55        3110       -   
45           1cc7cfca  2019-08-17T21:15:56        4030       -   
46           2dc29e21  2019-08-17T21:15:57        4020    True   
47           1cc7cfca  2019-08-17T21:15:57        4030       -   
48           2dc29e21  2019-08-17T21:16:00        4020   False   
49           1cc7cfca  2019-08-17T21:16:01        4030       -   
50           2dc29e21  2019-08-17T21:16:03        4020   False   
51           1cc7cfca  2019-08-17T21:16:03        4030       -   
52           2dc29e21  2019-08-17T21:16:04        4020    True   
53           1cc7cfca  2019-08-17T21:16:05        4030       -   
54           2dc29e21  2019-08-17T21:16:08        4020   False   
55           587b5989  2019-08-17T21:16:09        4070       -   
56           1cc7cfca  2019-08-17T21:16:11        4030       -   
57           2dc29e21  2019-08-17T21:16:11        4020   False   
58           c277e121  2019-08-17T21:16:12        3020       -   
59           b120f2ac  2019-08-17T21:16:12        202

__031aeedd7e24caef Dino Dive Game MAGMAPEAK v1.0__ 

...

event_id            timestamp  event_code correct  \
event_count                                                      
1            9c5ef70c  2019-08-12T04:40:53        2000       -   
2            0086365d  2019-08-12T04:40:57        4010       -   
3            a592d54e  2019-08-12T04:40:58        2020       -   
4            6cf7d25c  2019-08-12T04:40:58        3010       -   
5            f3cd5473  2019-08-12T04:41:01        4070       -   
6            f3cd5473  2019-08-12T04:41:02        4070       -   
7            f3cd5473  2019-08-12T04:41:05        4070       -   
8            15f99afc  2019-08-12T04:41:11        3110       -   
9            a5e9da97  2019-08-12T04:41:12        4100   False   
10           907a054b  2019-08-12T04:41:12        3020       -   
11           f3cd5473  2019-08-12T04:41:14        4070       -   
12           c51d8688  2019-08-12T04:41:14        3120       -   
13           2a444e03  2019-08-12T04:41:14        4030       -   
14           804ee27f  2019-08-12T04:41:15        4020   False   
15           a5e9da97  2019-08-12T04:41:17        4100   False   
16           907a054b  2019-08-12T04:41:17        3020       -   
17           c51d8688  2019-08-12T04:41:19        3120       -   
18           f3cd5473  2019-08-12T04:41:20        4070       -   
19           2a444e03  2019-08-12T04:41:21        4030       -   
20           e7561dd2  2019-08-12T04:41:22        4025    True   
21           2a444e03  2019-08-12T04:41:23        4030       -   
22           e7561dd2  2019-08-12T04:41:24        4025    True   
23           a5e9da97  2019-08-12T04:41:25        4100    True   
24           1c178d24  2019-08-12T04:41:27        2030       -   
25           250513af  2019-08-12T04:41:27        3021       -   
26           cf7638f3  2019-08-12T04:41:30        3121       -   
27           a592d54e  2019-08-12T04:41:30        2020       -   
28           6cf7d25c  2019-08-12T04:41:30        3010       -   
29           15f99afc  2019-08-12T04:41:32        3110       -   
30           a5e9da97  2019-08-12T04:41:32        4100   False   
31           907a054b  2019-08-12T04:41:32        3020       -   
32           f3cd5473  2019-08-12T04:41:34        4070       -   
33           c51d8688  2019-08-12T04:41:34        3120       -   
34           2a444e03  2019-08-12T04:41:35        4030       -   
35           804ee27f  2019-08-12T04:41:37        4020    True   
36           f3cd5473  2019-08-12T04:41:38        4070       -   
37           f3cd5473  2019-08-12T04:41:39        4070       -   
38           a5e9da97  2019-08-12T04:41:39        4100    True   
39           1c178d24  2019-08-12T04:41:41        2030       -   
40           250513af  2019-08-12T04:41:41        3021       -   
41           cf7638f3  2019-08-12T04:41:45        3121       -   
42           a592d54e  2019-08-12T04:41:45        2020       -   
43           6cf7d25c  2019-08-12T04:41:45        3010       -   
44           15f99afc  2019-08-12T04:41:47        3110       -   
45           2a444e03  2019-08-12T04:41:48        4030       -   
46           804ee27f  2019-08-12T04:41:49        4020    True   
47           f3cd5473  2019-08-12T04:41:50        4070       -   
48           f3cd5473  2019-08-12T04:41:51        4070       -   
49           a5e9da97  2019-08-12T04:41:52        4100    True   
50           1c178d24  2019-08-12T04:41:54        2030       -   
51           250513af  2019-08-12T04:41:54        3021       -   
52           cf7638f3  2019-08-12T04:41:59        3121       -   
53           a592d54e  2019-08-12T04:41:59        2020       -   
54           6cf7d25c  2019-08-12T04:41:59        3010       -   
55           15f99afc  2019-08-12T04:42:01        3110       -   
56           f3cd5473  2019-08-12T04:42:01        4070       -   
57           2a444e03  2019-08-12T04:42:02        4030       -   
58           bc8f2793  2019-08-12T04:42:04        4035       -   
59           2a444e03  2019-08-12T04:42:05        403

__85d0f88c0a12981e Air Show Game TREETOPCITY v1__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            15ba1109  2019-09-25T15:15:53        2000       -   
2            65abac75  2019-09-25T15:15:55        4010       -   
3            06372577  2019-09-25T15:16:00        2060       -   
4            f28c589a  2019-09-25T15:16:00        3010       -   
5            bcceccc6  2019-09-25T15:16:01        4070       -   
6            bcceccc6  2019-09-25T15:16:02        4070       -   
7            a1bbe385  2019-09-25T15:16:04        3110       -   
8            f28c589a  2019-09-25T15:16:04        3010       -   
9            bcceccc6  2019-09-25T15:16:06        4070       -   
10           bcceccc6  2019-09-25T15:16:06        4070       -   
11           bcceccc6  2019-09-25T15:16:07        4070       -   
12           bcceccc6  2019-09-25T15:16:07        4070       -   
13           bcceccc6  2019-09-25T15:16:09        4070       -   
14           a1bbe385  2019-09-25T15:16:09        3110       -   
15           f28c589a  2019-09-25T15:16:10        3010       -   
16           bcceccc6  2019-09-25T15:16:10        4070       -   
17           bcceccc6  2019-09-25T15:16:11        4070       -   
18           bcceccc6  2019-09-25T15:16:12        4070       -   
19           a1bbe385  2019-09-25T15:16:12        3110       -   
20           bcceccc6  2019-09-25T15:16:13        4070       -   
21           bcceccc6  2019-09-25T15:16:13        4070       -   
22           bcceccc6  2019-09-25T15:16:13        4070       -   
23           bcceccc6  2019-09-25T15:16:13        4070       -   
24           bcceccc6  2019-09-25T15:16:13        4070       -   
25           bcceccc6  2019-09-25T15:16:14        4070       -   
26           bcceccc6  2019-09-25T15:16:14        4070       -   
27           bcceccc6  2019-09-25T15:16:14        4070       -   
28           bcceccc6  2019-09-25T15:16:15        4070       -   
29           bcceccc6  2019-09-25T15:16:15        4070       -   
30           f28c589a  2019-09-25T15:16:16        3010       -   
31           a1bbe385  2019-09-25T15:16:18        3110       -   
32           d88ca108  2019-09-25T15:16:18        2070       -   
33           f28c589a  2019-09-25T15:16:18        3010       -   
34           bcceccc6  2019-09-25T15:16:19        4070       -   
35           bcceccc6  2019-09-25T15:16:19        4070       -   
36           bcceccc6  2019-09-25T15:16:20        4070       -   
37           bcceccc6  2019-09-25T15:16:20        4070       -   
38           bcceccc6  2019-09-25T15:16:23        4070       -   
39           a1bbe385  2019-09-25T15:16:24        3110       -   
40           bcceccc6  2019-09-25T15:16:24        4070       -   
41           bcceccc6  2019-09-25T15:16:24        4070       -   
42           bcceccc6  2019-09-25T15:16:25        4070       -   
43           bcceccc6  2019-09-25T15:16:26        4070       -   
44           bcceccc6  2019-09-25T15:16:27        4070       -   
45           bcceccc6  2019-09-25T15:16:27        4070       -   
46           bcceccc6  2019-09-25T15:16:27        4070       -   
47           bcceccc6  2019-09-25T15:16:27        4070       -   
48           f28c589a  2019-09-25T15:16:29        3010       -   
49           a1bbe385  2019-09-25T15:16:30        3110       -   
50           f28c589a  2019-09-25T15:16:30        3010       -   
51           bcceccc6  2019-09-25T15:16:30        4070       -   
52           bcceccc6  2019-09-25T15:16:30        4070       -   
53           a1bbe385  2019-09-25T15:16:32        3110       -   
54           f28c589a  2019-09-25T15:16:32        3010       -   
55           a1bbe385  2019-09-25T15:16:32        3110       -   
56           f28c589a  2019-09-25T15:16:32        3010       -   
57           a1bbe385  2019-09-25T15:16:32        3110       -   
58           f28c589a  2019-09-25T15:16:32        3010       -   
59           bcceccc6  2019-09-25T15:16:33        407

__19aeaab7016ba85d Crystals Rule Game TREETOPCITY v1.0__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            48349b14  2019-08-27T01:57:28        2000       -   
2            cc5087a3  2019-08-27T01:57:32        4010       -   
3            5154fc30  2019-08-27T01:57:33        3010       -   
4            5e3ea25a  2019-08-27T01:57:39        4070       -   
5            5e3ea25a  2019-08-27T01:57:41        4070       -   
6            5e3ea25a  2019-08-27T01:57:45        4070       -   
7            3babcb9b  2019-08-27T01:57:45        3110       -   
8            7cf1bc53  2019-08-27T01:57:45        2020       -   
9            5154fc30  2019-08-27T01:57:45        3010       -   
10           5e3ea25a  2019-08-27T01:57:46        4070       -   
11           5e3ea25a  2019-08-27T01:57:48        4070       -   
12           3babcb9b  2019-08-27T01:57:49        3110       -   
13           86c924c4  2019-08-27T01:57:51        4020   False   
14           5154fc30  2019-08-27T01:57:51        3010       -   
15           5e3ea25a  2019-08-27T01:57:52        4070       -   
16           3babcb9b  2019-08-27T01:57:53        3110       -   
17           5154fc30  2019-08-27T01:57:53        3010       -   
18           5e3ea25a  2019-08-27T01:57:53        4070       -   
19           3babcb9b  2019-08-27T01:57:54        3110       -   
20           5e3ea25a  2019-08-27T01:57:54        4070       -   
21           44cb4907  2019-08-27T01:57:54        3020       -   
22           5e3ea25a  2019-08-27T01:57:56        4070       -   
23           5e3ea25a  2019-08-27T01:57:56        4070       -   
24           5e3ea25a  2019-08-27T01:57:57        4070       -   
25           5e3ea25a  2019-08-27T01:57:57        4070       -   
26           5e3ea25a  2019-08-27T01:57:58        4070       -   
27           8b757ab8  2019-08-27T01:57:58        3120       -   
28           86c924c4  2019-08-27T01:57:59        4020    True   
29           5154fc30  2019-08-27T01:57:59        3010       -   
30           5e3ea25a  2019-08-27T01:57:59        4070       -   
31           5e3ea25a  2019-08-27T01:58:00        4070       -   
32           3babcb9b  2019-08-27T01:58:00        3110       -   
33           5154fc30  2019-08-27T01:58:00        3010       -   
34           3babcb9b  2019-08-27T01:58:01        3110       -   
35           5154fc30  2019-08-27T01:58:01        3010       -   
36           3babcb9b  2019-08-27T01:58:03        3110       -   
37           3ddc79c3  2019-08-27T01:58:03        3021       -   
38           e720d930  2019-08-27T01:58:06        3121       -   
39           3323d7e9  2019-08-27T01:58:06        2030       -   
40           7cf1bc53  2019-08-27T01:58:06        2020       -   
41           5154fc30  2019-08-27T01:58:06        3010       -   
42           5e3ea25a  2019-08-27T01:58:09        4070       -   
43           3babcb9b  2019-08-27T01:58:09        3110       -   
44           86c924c4  2019-08-27T01:58:10        4020   False   
45           5154fc30  2019-08-27T01:58:10        3010       -   
46           3babcb9b  2019-08-27T01:58:11        3110       -   
47           5154fc30  2019-08-27T01:58:11        3010       -   
48           3babcb9b  2019-08-27T01:58:12        3110       -   
49           5154fc30  2019-08-27T01:58:12        3010       -   
50           3babcb9b  2019-08-27T01:58:14        3110       -   
51           44cb4907  2019-08-27T01:58:14        3020       -   
52           5e3ea25a  2019-08-27T01:58:15        4070       -   
53           5e3ea25a  2019-08-27T01:58:15        4070       -   
54           5e3ea25a  2019-08-27T01:58:16        4070       -   
55           5e3ea25a  2019-08-27T01:58:17        4070       -   
56           5e3ea25a  2019-08-27T01:58:18        4070       -   
57           5e3ea25a  2019-08-27T01:58:18        4070       -   
58           8b757ab8  2019-08-27T01:58:18        3120       -   
59           86c924c4  2019-08-27T01:58:18        402

In [7]:
for game in test.title[test.type=="Assessment"].unique():
    show_game_session(train, game, ["coordinates"])

__c5c88cbef0dce5d9 Cart Balancer (Assessment) Assessment CRYSTALCAVES v1.0__ 

event_id            timestamp  event_code correct crystal_id  \
event_count                                                                 
1            7ad3efc6  2019-09-30T11:48:32        2000       -          -   
2            65a38bf7  2019-09-30T11:48:32        2020       -          -   
3            795e4a37  2019-09-30T11:48:32        3010       -          -   
4            828e68f9  2019-09-30T11:48:39        3110       -          -   
5            795e4a37  2019-09-30T11:48:51        3010       -          -   
6            828e68f9  2019-09-30T11:48:53        3110       -          -   
7            acf5c23f  2019-09-30T11:48:54        4070       -          -   
8            acf5c23f  2019-09-30T11:49:02        4070       -          -   
9            acf5c23f  2019-09-30T11:49:02        4070       -          -   
10           acf5c23f  2019-09-30T11:49:02        4070       -          -   
11           acf5c23f  2019-09-30T11:49:02        4070       -          -   
12           5e109ec3  2019-09-30T11:50:48        4030       -      gem08   
13           5c2f29ca  2019-09-30T11:50:49        4020       -      gem08   
14           5e109ec3  2019-09-30T11:50:50        4030       -      gem07   
15           5c2f29ca  2019-09-30T11:50:50        4020       -      gem07   
16           d122731b  2019-09-30T11:50:53        4100    True          -   
17           a8876db3  2019-09-30T11:50:53        3021       -          -   
18           ecaab346  2019-09-30T11:51:00        3121       -          -   
19           b74258a0  2019-09-30T11:51:00        2030       -          -   
20           b2e5b0f1  2019-09-30T11:51:00        2010       -          -   

                                                                                                                                                                                                                                                     crystals  \
event_count                                                                                                                                                                                                                                                     
1                                                                                                                                                                                                                                                           -   
2            [{'id': 'gem07', 'weight': 6}, {'id': 'gem05', 'weight': 4}, {'id': 'gem01', 'weight': 1}, {'id': 'gem03', 'weight': 3}, {'id': 'gem02', 'weight': 1}, {'id': 'gem08', 'weight': 6}, {'id': 'gem04', 'weight': 3}, {'id': 'gem06', 'weight': 4}]   
3                                                                                                                                                                                                                                                           -   
4                                                                                                                                                                                                                                                           -   
5                                                                                                                                                                                                                                                           -   
6                                                                                                                                                                                                                                                           -   
7                                                                                                                                                                                                                                                           -   
8    

__2c104319c9be467e Cauldron Filler (Assessment) Assessment MAGMAPEAK v1.0__ 

event_id            timestamp  event_code bucket    buckets  \
event_count                                                                
1            90d848e0  2019-09-07T16:20:05        2000      -          -   
2            923afab1  2019-09-07T16:20:06        3010      -          -   
3            532a2afb  2019-09-07T16:20:06        2020      -  [3, 1, 2]   
4            3ee399c3  2019-09-07T16:20:09        4070      -          -   
5            2dcad279  2019-09-07T16:20:10        3110      -          -   
6            3ee399c3  2019-09-07T16:20:11        4070      -          -   
7            37ee8496  2019-09-07T16:20:12        4030      3  [0, 1, 2]   
8            5348fd84  2019-09-07T16:20:13        4040      3  [3, 1, 2]   
9            3ee399c3  2019-09-07T16:20:14        4070      -          -   
10           3ee399c3  2019-09-07T16:20:14        4070      -          -   
11           3ee399c3  2019-09-07T16:20:15        4070      -          -   
12           3ee399c3  2019-09-07T16:20:15        4070      -          -   
13           3ee399c3  2019-09-07T16:20:15        4070      -          -   
14           3ee399c3  2019-09-07T16:20:16        4070      -          -   
15           3ee399c3  2019-09-07T16:20:16        4070      -          -   
16           3ee399c3  2019-09-07T16:20:16        4070      -          -   
17           3ee399c3  2019-09-07T16:20:16        4070      -          -   
18           3ee399c3  2019-09-07T16:20:16        4070      -          -   
19           37ee8496  2019-09-07T16:20:16        4030      3  [0, 1, 2]   
20           30614231  2019-09-07T16:20:16        4020      3  [0, 1, 2]   
21           3ee399c3  2019-09-07T16:20:16        4070      -          -   
22           3ee399c3  2019-09-07T16:20:16        4070      -          -   
23           3ee399c3  2019-09-07T16:20:16        4070      -          -   
24           3ee399c3  2019-09-07T16:20:16        4070      -          -   
25           3ee399c3  2019-09-07T16:20:16        4070      -          -   
26           3ee399c3  2019-09-07T16:20:16        4070      -          -   
27           3ee399c3  2019-09-07T16:20:16        4070      -          -   
28           3ee399c3  2019-09-07T16:20:16        4070      -          -   
29           3ee399c3  2019-09-07T16:20:16        4070      -          -   
30           3ee399c3  2019-09-07T16:20:18        4070      -          -   
31           3ee399c3  2019-09-07T16:20:18        4070      -          -   
32           3ee399c3  2019-09-07T16:20:19        4070      -          -   
33           37ee8496  2019-09-07T16:20:20        4030      1  [0, 0, 2]   
34           5348fd84  2019-09-07T16:20:20        4040      1  [0, 1, 2]   
35           3ee399c3  2019-09-07T16:20:21        4070      -          -   
36           3ee399c3  2019-09-07T16:20:22        4070      -          -   
37           3ee399c3  2019-09-07T16:20:22        4070      -          -   
38           3ee399c3  2019-09-07T16:20:22        4070      -          -   
39           37ee8496  2019-09-07T16:20:22        4030      1  [0, 0, 2]   
40           5348fd84  2019-09-07T16:20:22        4040      1  [0, 1, 2]   
41           3ee399c3  2019-09-07T16:20:22        4070      -          -   
42           3ee399c3  2019-09-07T16:20:22        4070      -          -   
43           3ee399c3  2019-09-07T16:20:22        4070      -          -   
44           37ee8496  2019-09-07T16:20:22        4030      1  [0, 0, 2]   
45           5348fd84  2019-09-07T16:20:22        4040      1  [0, 1, 2]   
46           3ee399c3  2019-09-07T16:20:23        4070      -          -   
47           3ee399c3  2019-09-07T16:20:23        4070      -          -   
48           37ee8496  2019-09-07T16:20:23        4030      1  [0, 0, 2]   
49           3ee399c3  2019-09-07T16:20:23        4070      -          -   
50           30614231  2019-09-07T16:20:23        4020      1  [0, 0, 2]   
51           3ee399c3  2019-09-07T16:20:23        4070      -

__b02ff83a9fa1c809 Chest Sorter (Assessment) Assessment CRYSTALCAVES v1.0__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            5b49460a  2019-09-13T19:59:34        2000       -   
2            155f62a4  2019-09-13T19:59:34        2020       -   
3            3dcdda7f  2019-09-13T19:59:34        3010       -   
4            3ccd3f02  2019-09-13T19:59:37        3110       -   
5            3dcdda7f  2019-09-13T19:59:37        3010       -   
6            bd612267  2019-09-13T19:59:38        4070       -   
7            3ccd3f02  2019-09-13T19:59:39        3110       -   
8            3dcdda7f  2019-09-13T19:59:39        3010       -   
9            a8efe47b  2019-09-13T19:59:40        4030       -   
10           3d0b9317  2019-09-13T19:59:40        4040       -   
11           a8efe47b  2019-09-13T19:59:41        4030       -   
12           562cec5f  2019-09-13T19:59:42        4025       -   
13           3ccd3f02  2019-09-13T19:59:42        3110       -   
14           a8efe47b  2019-09-13T19:59:42        4030       -   
15           562cec5f  2019-09-13T19:59:44        4025       -   
16           bd612267  2019-09-13T19:59:47        4070       -   
17           93b353f2  2019-09-13T19:59:48        4100   False   
18           ea296733  2019-09-13T19:59:48        3020       -   
19           a8efe47b  2019-09-13T19:59:49        4030       -   
20           df4fe8b6  2019-09-13T19:59:50        3120       -   
21           562cec5f  2019-09-13T19:59:51        4025       -   
22           a8efe47b  2019-09-13T19:59:52        4030       -   
23           562cec5f  2019-09-13T19:59:53        4025       -   
24           a8efe47b  2019-09-13T19:59:57        4030       -   
25           562cec5f  2019-09-13T19:59:58        4025       -   
26           a8efe47b  2019-09-13T20:00:00        4030       -   
27           562cec5f  2019-09-13T20:00:01        4025       -   
28           a8efe47b  2019-09-13T20:00:04        4030       -   
29           562cec5f  2019-09-13T20:00:05        4025       -   
30           a8efe47b  2019-09-13T20:00:06        4030       -   
31           562cec5f  2019-09-13T20:00:07        4025       -   
32           a8efe47b  2019-09-13T20:00:07        4030       -   
33           0db6d71d  2019-09-13T20:00:08        4020    True   
34           a8efe47b  2019-09-13T20:00:09        4030       -   
35           0db6d71d  2019-09-13T20:00:09        4020   False   
36           a8efe47b  2019-09-13T20:00:11        4030       -   
37           562cec5f  2019-09-13T20:00:12        4025       -   
38           a8efe47b  2019-09-13T20:00:15        4030       -   
39           562cec5f  2019-09-13T20:00:15        4025       -   
40           93b353f2  2019-09-13T20:00:16        4100   False   
41           ea296733  2019-09-13T20:00:16        3020       -   
42           df4fe8b6  2019-09-13T20:00:18        3120       -   
43           a8efe47b  2019-09-13T20:00:19        4030       -   
44           562cec5f  2019-09-13T20:00:20        4025       -   
45           93b353f2  2019-09-13T20:00:21        4100   False   
46           ea296733  2019-09-13T20:00:21        3020       -   
47           df4fe8b6  2019-09-13T20:00:23        3120       -   
48           a8efe47b  2019-09-13T20:00:24        4030       -   
49           562cec5f  2019-09-13T20:00:24        4025       -   
50           93b353f2  2019-09-13T20:00:27        4100   False   
51           ea296733  2019-09-13T20:00:27        3020       -   
52           bd612267  2019-09-13T20:00:28        4070       -   
53           df4fe8b6  2019-09-13T20:00:28        3120       -   
54           bd612267  2019-09-13T20:00:29        4070       -   
55           bd612267  2019-09-13T20:00:29        4070       -   
56           bd612267  2019-09-13T20:00:30        4070       -   
57           a8efe47b  2019-09-13T20:00:31        4030       -   
58           0db6d71d  2019-09-13T20:00:32        4020    True   
59           a8efe47b  2019-09-13T20:00:33        403

__d156a6e6f0ada77d Mushroom Sorter (Assessment) Assessment TREETOPCITY v1.0__ 

event_id            timestamp  event_code correct  \
event_count                                                      
1            3bfd1a65  2019-09-12T16:00:18        2000       -   
2            db02c830  2019-09-12T16:00:18        2025       -   
3            a1e4395d  2019-09-12T16:00:18        3010       -   
4            a52b92d5  2019-09-12T16:00:22        3110       -   
5            a1e4395d  2019-09-12T16:00:22        3010       -   
6            28ed704e  2019-09-12T16:00:22        4025       -   
7            a52b92d5  2019-09-12T16:00:22        3110       -   
8            9d29771f  2019-09-12T16:00:22        3021       -   
9            c74f40cd  2019-09-12T16:00:23        3121       -   
10           7da34a02  2019-09-12T16:00:23        4070       -   
11           28ed704e  2019-09-12T16:00:25        4025       -   
12           9d29771f  2019-09-12T16:00:25        3021       -   
13           c74f40cd  2019-09-12T16:00:25        3121       -   
14           28ed704e  2019-09-12T16:00:26        4025       -   
15           9d29771f  2019-09-12T16:00:26        3021       -   
16           7da34a02  2019-09-12T16:00:27        4070       -   
17           c74f40cd  2019-09-12T16:00:27        3121       -   
18           83c6c409  2019-09-12T16:00:27        2035       -   
19           3dfd4aa4  2019-09-12T16:00:27        2020       -   
20           a1e4395d  2019-09-12T16:00:27        3010       -   
21           7da34a02  2019-09-12T16:00:29        4070       -   
22           7da34a02  2019-09-12T16:00:30        4070       -   
23           a52b92d5  2019-09-12T16:00:31        3110       -   
24           7da34a02  2019-09-12T16:00:32        4070       -   
25           7da34a02  2019-09-12T16:00:32        4070       -   
26           7da34a02  2019-09-12T16:00:33        4070       -   
27           fbaf3456  2019-09-12T16:00:34        4030       -   
28           c7128948  2019-09-12T16:00:34        4040       -   
29           7da34a02  2019-09-12T16:00:35        4070       -   
30           7da34a02  2019-09-12T16:00:35        4070       -   
31           7da34a02  2019-09-12T16:00:36        4070       -   
32           7da34a02  2019-09-12T16:00:37        4070       -   
33           7da34a02  2019-09-12T16:00:37        4070       -   
34           7da34a02  2019-09-12T16:00:37        4070       -   
35           a1e4395d  2019-09-12T16:00:43        3010       -   
36           a52b92d5  2019-09-12T16:00:45        3110       -   
37           fbaf3456  2019-09-12T16:00:46        4030       -   
38           5f0eb72c  2019-09-12T16:00:47        4020   False   
39           fbaf3456  2019-09-12T16:00:48        4030       -   
40           5f0eb72c  2019-09-12T16:00:49        4020    True   
41           fbaf3456  2019-09-12T16:00:49        4030       -   
42           5f0eb72c  2019-09-12T16:00:50        4020   False   
43           7da34a02  2019-09-12T16:00:51        4070       -   
44           fbaf3456  2019-09-12T16:00:52        4030       -   
45           5f0eb72c  2019-09-12T16:00:53        4020    True   
46           7da34a02  2019-09-12T16:00:53        4070       -   
47           fbaf3456  2019-09-12T16:00:54        4030       -   
48           5f0eb72c  2019-09-12T16:00:54        4020    True   
49           fbaf3456  2019-09-12T16:00:56        4030       -   
50           5f0eb72c  2019-09-12T16:00:56        4020    True   
51           a1e4395d  2019-09-12T16:00:56        3010       -   
52           25fa8af4  2019-09-12T16:00:57        4100    True   
53           a52b92d5  2019-09-12T16:00:57        3110       -   
54           9d29771f  2019-09-12T16:00:57        3021       -   
55           c74f40cd  2019-09-12T16:01:02        3121       -   
56           6c930e6e  2019-09-12T16:01:02        2030       -   
57           a5be6304  2019-09-12T16:01:06        2010       -   

                                                                                 description  \
event_count           

__8601aeaf34928818 Bird Measurer (Assessment) Assessment TREETOPCITY v1.0__ 

event_id            timestamp  event_code bird_height  \
event_count                                                          
1            f56e0afc  2019-10-08T01:09:10        2000           -   
2            ec138c1c  2019-10-08T01:09:10        2020           -   
3            1375ccb7  2019-10-08T01:09:10        3010           -   
4            bdf49a58  2019-10-08T01:09:15        3110           -   
5            51102b85  2019-10-08T01:09:17        4030           -   
6            4a4c3d21  2019-10-08T01:09:18        4025           8   
7            51102b85  2019-10-08T01:09:19        4030           -   
8            4a4c3d21  2019-10-08T01:09:20        4025           5   
9            51102b85  2019-10-08T01:09:22        4030           -   
10           4a4c3d21  2019-10-08T01:09:23        4025           4   
11           1375ccb7  2019-10-08T01:09:23        3010           -   
12           bdf49a58  2019-10-08T01:09:26        3110           -   
13           17113b36  2019-10-08T01:09:27        4110           -   
14           ad2fc29c  2019-10-08T01:09:27        3020           -   
15           e37a2b78  2019-10-08T01:09:30        3120           -   
16           17113b36  2019-10-08T01:13:52        4110           -   
17           ad2fc29c  2019-10-08T01:13:52        3020           -   
18           51102b85  2019-10-08T01:13:54        4030           -   
19           e37a2b78  2019-10-08T01:13:55        3120           -   
20           4a4c3d21  2019-10-08T01:13:55        4025           4   
21           a16a373e  2019-10-08T01:13:56        4070           -   
22           a16a373e  2019-10-08T01:13:57        4070           -   
23           51102b85  2019-10-08T01:13:58        4030           -   
24           4a4c3d21  2019-10-08T01:13:58        4025           5   
25           51102b85  2019-10-08T01:13:59        4030           -   
26           4a4c3d21  2019-10-08T01:14:00        4025           5   
27           17113b36  2019-10-08T01:14:00        4110           -   
28           ad2fc29c  2019-10-08T01:14:00        3020           -   
29           e37a2b78  2019-10-08T01:14:03        3120           -   
30           a16a373e  2019-10-08T01:14:05        4070           -   
31           51102b85  2019-10-08T01:14:06        4030           -   
32           4a4c3d21  2019-10-08T01:14:08        4025           8   
33           51102b85  2019-10-08T01:14:09        4030           -   
34           4a4c3d21  2019-10-08T01:14:10        4025           5   
35           51102b85  2019-10-08T01:14:12        4030           -   
36           4a4c3d21  2019-10-08T01:14:12        4025           4   
37           51102b85  2019-10-08T01:14:12        4030           -   
38           4a4c3d21  2019-10-08T01:14:14        4025           4   
39           a16a373e  2019-10-08T01:14:16        4070           -   
40           17113b36  2019-10-08T01:14:17        4110           -   
41           45d01abe  2019-10-08T01:14:17        3021           -   
42           7525289a  2019-10-08T01:14:20        3121           -   
43           f6947f54  2019-10-08T01:14:20        2030           -   
44           ec138c1c  2019-10-08T01:14:20        2020           -   
45           1375ccb7  2019-10-08T01:14:20        3010           -   
46           bdf49a58  2019-10-08T01:14:25        3110           -   
47           1375ccb7  2019-10-08T01:14:25        3010           -   
48           bdf49a58  2019-10-08T01:14:30        3110           -   
49           51102b85  2019-10-08T01:14:32        4030           -   
50           8fee50e2  2019-10-08T01:14:33        4020           -   
51           51102b85  2019-10-08T01:14:33        4030           -   
52           8fee50e2  2019-10-08T01:14:34        4020           -   
53           a16a373e  2019-10-08T01:14:34        4070           -   
54           51102b85  2019-10-08T01:14:35        4030           -   
55           8fee50e2  2019-10-08T01:14:36        4020           -   
56           51102b85  